# Actividad: Entornos Multiagentes

**Integrantes:**
- Karla González Sánchez A01541526
- Luis Ángel Alba Alfaro A01640314
- María Fernanda Elizalde Macías A01634135
- Sofía del Pilar Batiz Martínez A01634125

Modelación de sistemas multiagentes con gráficas computacionales  
Gamaliel Abisay Palomo Briones  
Omar Mendoza Montoya  
Guillermo Gabriel Rivas Aguilar  
14 de noviembre de 2022  

Importar librerías

In [551]:
import agentpy as ap
import random

## Problema 1

Definir la clase

In [552]:
class Player(ap.Agent):
    def setup(self):
        self.before = None
        self.direction = None
        self.wins = 0
    
    def getNewDirection(self):
        self.before = self.direction

        #Juego
        #0 -> abajo, 1 -> arriba
        match self.id:
            case 1:
                self.direction = random.randint(0, 1)
            case 2:
                self.direction = 0
            case 3:
                if self.model.last_winner is not None:
                    before_player = self.model.agents[self.model.last_winner - 1].before
                    self.direction = before_player
                elif self.model.t == 0:
                    self.direction = 1
            case 4:
                player1_before = self.model.agents[0].before
                if player1_before is not None:
                    if player1_before == 1:
                        self.direction = 0
                    else:
                        self.direction = 1
                elif self.model.t == 0:
                    self.direction = random.randint(0, 1)

Definir el modelo

In [553]:
class Disaperejo(ap.Model):
    def findWinner(self):
        count = 0
        self.winner = None

        for player in self.agents:
            if player.direction == 0:
                count += 1
        
        for player in self.agents:
            if count == 1 and player.direction == 0:
                player.wins += 1
                self.last_winner = player.id
                break
            elif count == 3 and player.direction == 1:
                player.wins += 1
                self.last_winner = player.id
                break
    
    def setup(self):
        self.last_winner = None
        self.agents = ap.AgentList(self, 4, Player)
        self.agents.getNewDirection()
        self.findWinner()
    
    def step(self):
        self.agents.getNewDirection()
        self.last_winner = None
        self.findWinner()
    
    def update(self):
        self.agents.record('direction')
        self.agents.record('wins')
        

In [554]:
games = 1000
parameters = {
    'steps': games - 1
}

Simulación

In [555]:
model = Disaperejo(parameters)
results = model.run()

Completed: 999 steps
Run time: 0:00:00.021999
Simulation finished


Impresión de resultados

In [556]:
res_player1 = results.variables.Player.wins[1][model.p['steps']]
res_player2 = results.variables.Player.wins[2][model.p['steps']]
res_player3 = results.variables.Player.wins[3][model.p['steps']]
res_player4 = results.variables.Player.wins[4][model.p['steps']]
res_tied = games - (res_player1 + res_player2 + res_player3 + res_player4)

In [557]:
print(f"NUMERO DE JUEGOS: {games}\n"
     f"Jugador -> Total de partidas ganadas:\n"
     f"1 -> {res_player1}\n"
     f"2 -> {res_player2}\n"
     f"3 -> {res_player3}\n"
     f"4 -> {res_player4}\n"
     f"Empates -> {res_tied}")

NUMERO DE JUEGOS: 1000
Jugador -> Total de partidas ganadas:
1 -> 120
2 -> 152
3 -> 121
4 -> 96
Empates -> 511


## Problema 2

In [558]:
import matplotlib.pyplot as plt
import seaborn as sns
import IPython
import random

Definicion del modelo

In [559]:
class ForestModel(ap.Model):

    def setup(self):

        # Create agents (trees)
        n_trees = int(self.p['Tree density'] * (self.p.size**2)) #numero de arboles
        trees = self.agents = ap.AgentList(self, n_trees // 3)
        self.slow_trees = ap.AgentList(self, n_trees // 3)
        self.slower_trees = ap.AgentList(self, n_trees - n_trees // 3 * 2)

        # Create grid (forest)
        self.forest = ap.Grid(self, [self.p.size]*2, track_empty=True)
        self.forest.add_agents(trees, random=True, empty=True)

        self.forest.add_agents(self.slow_trees, random=True, empty=True)
        self.forest.add_agents(self.slower_trees, random=True, empty=True)

        # Initiate a dynamic variable for all trees
        # Condition 0: Alive, 1: Burning, 2: Burned
        self.agents.condition = 0
        self.slow_trees.condition = 0
        self.slower_trees.condition = 0

        self.agents.hp = 1
        self.slow_trees.hp = 2
        self.slower_trees.hp = 3

        # Start a fire from the left side of the grid
        randX = random.randint(1, self.p.size - 1)
        randY = random.randint(1, self.p.size - 1)
        unfortunate_trees = self.forest.agents[randX:randX + 5, randY:randY + 5]
        unfortunate_trees.condition = 1

       
    def step(self):

        # Select burning trees
        burning_trees1 = self.agents.select(self.agents.condition == 1)
        burning_trees2 = self.slow_trees.select(self.slow_trees.condition == 1)
        burning_trees3 = self.slower_trees.select(self.slower_trees.condition == 1)

        # Spread fire
        for tree in burning_trees1 + burning_trees2 + burning_trees3:
            for neighbor in self.forest.neighbors(tree):
                if neighbor.condition == 0:
                    neighbor.condition = 1 # Neighbor starts burning # Tree burns out
            tree.hp -= 1
            if tree.hp <= 0:
                tree.condition = 2
            
        
        self.agents.hp -= 1
        self.slow_trees.hp -= 1
        self.slower_trees.hp -= 1

        if  self.agents.hp == 0:
            burning_trees1.condition = 2
        if self.slow_trees.hp == 0:
            burning_trees2.condition = 2
        if self.slower_trees.hp == 0:
            burning_trees3.condition = 2


        # Stop simulation if no fire is left
        if len(burning_trees1) == 0 and len(burning_trees2) == 0 and len(burning_trees3) == 0:
            self.stop()

    def end(self):

        # Document a measure at the end of the simulation
        burned_trees1 = len(self.agents.select(self.agents.condition == 2))
        burned_trees2 = len(self.slow_trees.select(self.slow_trees.condition == 2))
        burned_trees3 = len(self.slower_trees.select(self.slower_trees.condition == 2))
        self.report('Percentage of burned trees',
                    (burned_trees1 + burned_trees2 + burned_trees3) / len(self.agents))

Animacion

In [560]:
parameters = {
    'Tree density': 0.6, # Percentage of grid covered by trees
    'size': 50, # Height and length of the grid
    'steps': 100,
}

In [561]:
def animation_plot(model, ax):
    attr_grid = model.forest.attr_grid('condition')
    color_dict = {0:'#7FC97F', 1:'#d62c2c', 2:'#e5e5e5', None:'#d5e5d5'}
    ap.gridplot(attr_grid, ax=ax, color_dict=color_dict, convert=True)
    ax.set_title(f"Simulation of a forest fire\n"
                 f"Time-step: {model.t}, Trees left: "
                 f"{len(model.agents.select(model.agents.condition == 0)) + len(model.slow_trees.select(model.agents.condition == 0)) + len(model.slower_trees.select(model.agents.condition == 0))}")

fig, ax = plt.subplots()
model = ForestModel(parameters)
animation = ap.animate(model, fig, ax, animation_plot)
IPython.display.HTML(animation.to_jshtml(fps=15))

## Problema 3

In [562]:
import agentpy as ap
import random
import matplotlib.pyplot as plt
import seaborn as sns
import IPython

Definir las coordenadas de los posibles movimientos:

In [563]:
moves = [
    (-1,-1),(-1,0),(-1,1),
    (0,-1),(0,1),(0,0),
    (1,-1),(1,1),(1,0),
]

Definición del modelo

In [564]:
class VacuumModel(ap.Model):

    def setup(self):
        
        #Crear agentes
        n_trash = int((self.p['density'] * self.p.height * self.p.length))
        self.trash = self.agents = ap.AgentList(self, n_trash)
        self.robots = ap.AgentList(self, self.p['Number of robots'])

        #Grid
        self.area = ap.Grid(self, (self.p.height, self.p.length), track_empty=True)
        self.area.add_agents(self.trash, random=True, empty=True)

        #Agregar agentes
        self.area.add_agents(self.robots, random=True, empty=False)

        #Condiciones de los robots
        # 0 -> Sucio, 1 -> Robot, 2 -> Limpio
        self.trash.condition = 0
        self.robots.condition = 1

        self.count = 0


    def step(self):
        trash_cells = self.trash.select(self.trash.condition == 0)
        for robot in self.robots:
            for neighbor in self.area.neighbors(robot):
                if neighbor.condition == 0:
                    neighbor.condition = 2
                    break
            rand_move = random.choice(moves)
            self.area.move_by(robot, rand_move)
            self.count += 1
        
        #Termina simulacion
        if len(trash_cells) == 0:
            self.stop()
    
    def end(self):
        #self.report('Tiempo necesario',)
        self.record('Porcentaje de celdas limpias', len(self.agents.select(self.agents.condition == 2)) / len(self.agents) * 100)
        self.record('Movimientos', self.count)

Simulación

In [565]:
parameters = {
    'height': 10,
    'length': 20,
    'Number of robots': ap.IntRange(5, 30),
    'density': 0.3,
    'steps': 200
}

sample = ap.Sample(parameters, n=1)

In [566]:
def animation_plot(model, ax):
    attr_grid = model.area.attr_grid('condition')
    color_dict = {0: '#21130d', 1:'#d62c2c', 2:'#d5e5d5', None:'#d5e5d5'}
    ap.gridplot(attr_grid, ax=ax, color_dict=color_dict, convert=True)
    ax.set_title(f"Simulacion de Robots Limpiadores\n"
                 f"Time-step: {model.t}, Celdas limpias: "
                 f"{len(model.agents.select(model.agents.condition == 2))}\n"
                 f"Porcetaje de celdad limpias: "
                 f"{len(model.agents.select(model.agents.condition == 2)) / len(model.agents) * 100:.2f}%\n"
                 f"Pasos totales: {model.count}")

fig, ax = plt.subplots()
model = VacuumModel(parameters)
animation = ap.animate(model, fig, ax, animation_plot)
IPython.display.HTML(animation.to_jshtml(fps=15))